# Exploración

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import ast
from termcolor import colored

In [2]:
train = pd.read_csv('Datos/tsd_train.csv', 
                    converters={'spans':ast.literal_eval})
train.head()

spans  \
0  [8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19,...   
1                       [33, 34, 35, 36, 37, 38, 39]   
2                                       [0, 1, 2, 3]   
3          [7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17]   
4                       [32, 33, 34, 35, 36, 37, 38]   

                                                text  
0  Another violent and aggressive immigrant killi...  
1  I am 56 years old, I am not your fucking junio...  
2                  Damn, a whole family. Sad indeed.  
3  What a knucklehead. How can anyone not know th...  
4  "who do you think should do the killing?"\n\nA...

In [3]:
test = pd.read_csv('Datos/tsd_trial.csv', 
                   converters={'spans':ast.literal_eval})
test.head()

spans  \
0  [15, 16, 17, 18, 19, 27, 28, 29, 30, 31]   
1                  [29, 30, 31, 32, 33, 34]   
2            [166, 167, 168, 169, 170, 171]   
3                  [87, 88, 89, 90, 91, 92]   
4                                        []   

                                                text  
0  Because he's a moron and a bigot. It's not any...  
1  How about we stop protecting idiots and let na...  
2  If people  were  smart, they would  Boycott th...  
3  Trump Claimed that Russia will never invade th...  
4  As long as your willing to pay a lot more for ...

In [4]:
def color_toxic_words(index, text):
    colored_string = ''
    for i,x in enumerate(text):
        if i in index:
            colored_string += colored(x, on_color='on_red')
        else:
            colored_string += colored(x)
            
    return colored_string

In [5]:
for i,(index,text) in enumerate(train.values[0:5]):
    print('{} - '.format(i) + color_toxic_words(index, text) + '\n'*2)

0 - Another violent and aggressive immigrant killing a innocent and intelligent US Citizen.... Sarcasm


1 - I am 56 years old, I am not your fucking junior pal. What you are saying makes no sense. I don't know what you are basing this on. The cheap black market crap is still coming up from Mexican nationals, and the good stuff from BC and Humbolt.  The I5 corridor is still just as busy, and they are still making a ton of money. Nothing has really changed except that the legal market has made it easy for anyone of legal age to buy it.  And the legal market is controlled by corporate growers with million dollar facilities, or a co-op of smaller growers. The Federal government "war on drugs" really has no impact on the legal market in Oregon. I don't see any glutton of weed, whatever that means.


2 - Damn, a whole family. Sad indeed.


3 - What a knucklehead. How can anyone not know this would be offensive??


4 - "who do you think should do the killing?"

Anyone and everyone. This is a

## ¿Mal etiquetados?

En algunas oraciones pone los espacios, comas y otros signos como caracteres tóxicos, hay que tener cuidado y al final concatenarlos si es que hay dos o más palabras tóxicas juntas. 

In [6]:
very_toxic = [i for i,x in zip(train.index, train['spans']) if len(x)>100][0:5]

for i,(index,text) in zip(very_toxic, train.values[very_toxic]):
    print('{} - '.format(i) + color_toxic_words(index, text) + '\n'*2)

158 - These idiotic studies are upsetting. Where is the information that is surprising. Any person in any walk of like could and would state these (study) results?


159 - [To say that juxtaposing and making the same a massacre and overtly implying that someone had something to do with that massacre is mere "negligence" is absolutely asinine]
You confer what is determined based upon the evidence is "extremely silly or stupid?"  Is that how you see federal courts and judges function?
[Those "journalists" knew one thing had nothing to do with the other]
What are you waiting for?  You better call Palin and tell her you have evidence that proves the "journalists" knew that the two were not connected because that'll prove there was actual malice.
Wait.  Why don't I hear you dialing?
[Your unrelated SCOTUS case is cute]
Let me get this straight.  The judge in this article used exactly the standard but you deem it as "unrelated?"
You sir, are in complete and completely irrational denial.  It 

Y hay otros que definitivamente están mal etiquetados, donde no ponen lenguaje tóxico donde realmente sí lo hay.

In [7]:
actually_toxic = [27, 60, 82, 134, 382]

for index,text in train.values[actually_toxic]:
    print(color_toxic_words(index, text) + '\n'*2)

The malignant narcissist, mentally deranged sociopath, bigot, rascist, disingenuous blowhard and pathological liar, has now certified himself as a fascist. How much longer before his GOP sycophants and suckees say, "Enough!", and demand this repugnant, excrement-spewing fool's ouster?


the is NO CONSENSUS you ignorant loser, NONE, nothing but debate, thousands of scientist do not agree period, we dont need to move from anything other than left wing stupidity like yours.


aa nadda showing the usual stupidity, its clowns like you that live outside reality, see pal canada needs the usa, the usa does not need us. , dont get me wrong, trudeau an ignorant child with no leadership skills doing real damage to canada with bs like carbon taxes...


Try reading my entire comment again, except slower, and then take a few moments for reflection, days if need be. If by then you still don't understand that the Trumpster is Putins bitch, you'll never get it.


You are just a stick buthole!




# Preprocesamiento

Primero sería mejor tener las palabras tóxicas que los caracteres, también hay que tener cuidado cuando marcan un espacio o algún signo de puntuación como tóxico. También hay que pasar todo a minúscula y hacer el análisis en minúscula.

In [8]:
import string

In [9]:
def remove_symbols(index, text):
    """
    Remueve los índices que corresponden a símbolos 'no tóxicos', como espacios en blanco
    comas, puntos, etc.
    """
    index_clean = []   
    for i in index:
        x = text[i]
        if x not in (string.punctuation + string.whitespace):
            index_clean.append(i)
                        
    return index_clean

In [10]:
text = 'puto el que lo lea!!!'
index = np.arange(len(text)).tolist()

print(color_toxic_words(index, text))
print(color_toxic_words(remove_symbols(index, text), text))

puto el que lo lea!!!
puto el que lo lea!!!


In [11]:
indices_clean = [remove_symbols(index, text) for index,text in 
                 zip(train['spans'], train['text'])]

train['spans_clean'] = indices_clean

In [12]:
actually_toxic = [i for i,x in zip(train.index, train['spans']) if len(x)>100][0:3]

for i, (index,text,index_clean) in zip(actually_toxic, train.values[actually_toxic]):
    print('{} - '.format(i) + color_toxic_words(index, text))
    print('{} - '.format(i) + color_toxic_words(index_clean, text) + '\n'*2)

158 - These idiotic studies are upsetting. Where is the information that is surprising. Any person in any walk of like could and would state these (study) results?
158 - These idiotic studies are upsetting. Where is the information that is surprising. Any person in any walk of like could and would state these (study) results?


159 - [To say that juxtaposing and making the same a massacre and overtly implying that someone had something to do with that massacre is mere "negligence" is absolutely asinine]
You confer what is determined based upon the evidence is "extremely silly or stupid?"  Is that how you see federal courts and judges function?
[Those "journalists" knew one thing had nothing to do with the other]
What are you waiting for?  You better call Palin and tell her you have evidence that proves the "journalists" knew that the two were not connected because that'll prove there was actual malice.
Wait.  Why don't I hear you dialing?
[Your unrelated SCOTUS case is cute]
Let me get

También pasemos a minúscula el texto para el entrenamiento.

In [13]:
train['text'] = train['text'].apply(lambda x:x.lower())

# Modelos

## Hidden Markov Model

In [14]:
import nltk
from nltk.corpus import treebank
from nltk.tag import HiddenMarkovModelTrainer
from nltk.tokenize import word_tokenize

In [15]:
# Train data - pretagged
# train_data = treebank.tagged_sents()[:3000]

# trainer = HiddenMarkovModelTrainer()
# tagger = trainer.train_supervised(train_data)

# tagger.tag('Nobody expects the Spanish Inquisition!'.split())

In [16]:
def separate_words(indices):
    """
    Separa los índices por palabras.
    """
    toxic_words_indices = []
    m = 0
    for i,(j,k) in enumerate(zip(indices[0:-1], indices[1:])):
        if k-j != 1:
            toxic_words_indices.append(indices[m:i+1])
            m = i+1
    toxic_words_indices.append(indices[m:])
    
    return toxic_words_indices    

In [17]:
text = 'puto el que lo lea!!!'
index = np.arange(len(text)).tolist()

separated_indices = separate_words(remove_symbols(index, text))
print([(text[i[0]:i[-1]+1], i) for i in separated_indices])

[('puto', [0, 1, 2, 3]), ('el', [5, 6]), ('que', [8, 9, 10]), ('lo', [12, 13]), ('lea', [15, 16, 17])]


En nuestro caso debemos etiquetar en `toxic` y `non_toxic`.

In [18]:
train_data = []
for index, text in zip(train['spans_clean'], train['text']):
    toxic_words = [text[i[0]:i[-1]+1] for i in separate_words(index) if len(index) > 0]
#     print(toxic_words)
    
    tokens = word_tokenize(text)
    tagged_tokens = []
    
    for token in tokens:
        if token in toxic_words:
            tagged_tokens.append((token, 'toxic'))
            # Removemos en caso de que se repita posteriormente pero esté como 'non_toxic'
            toxic_words.remove(token) 
        else:
            tagged_tokens.append((token, 'non_toxic'))
            
    train_data.append(tagged_tokens)

In [19]:
trainer = HiddenMarkovModelTrainer()
tagger_HMM = trainer.train_supervised(train_data)

Ahora hagamos algunos experimentos.

In [20]:
tagger_HMM.tag(word_tokenize('fucking piece of shit, suck my dick'))

[('fucking', 'toxic'),
 ('piece', 'toxic'),
 ('of', 'toxic'),
 ('shit', 'toxic'),
 (',', 'non_toxic'),
 ('suck', 'toxic'),
 ('my', 'toxic'),
 ('dick', 'toxic')]

In [21]:
tagger_HMM.tag(word_tokenize('nice day, my dear nigger'))

[('nice', 'non_toxic'),
 ('day', 'non_toxic'),
 (',', 'non_toxic'),
 ('my', 'non_toxic'),
 ('dear', 'non_toxic'),
 ('nigger', 'toxic')]

Pero para la competencia necesitamos los índices, así que hagámoslo así.

In [22]:
def get_index_toxic_words(sentence, tagged_sentence):
    toxic_indices = []   
    m = 0
    for word_tag in tagged_sentence:
        word, tag = word_tag    
        if tag == 'toxic':
            # Si la palabra tóxica aparece 2 o más veces ésto solo dará la primera 
            # aparición, hay que arreglar eso pero por lo mientras sirve
            # word_indices = [sentence.find(word) + i for i in range(len(word))]
            # toxic_indices.append(word_indices)
            
            # Así parece evitar el problema de la palabra repetida
            word_indices = [m + sentence[m:].find(word) + i for i in range(len(word))]
            toxic_indices.append(word_indices)
            m += sentence[m:].find(word) + len(word) + 1
            
    toxic_indices = [val for sublist in toxic_indices for val in sublist]
        
    return toxic_indices

In [23]:
text = 'fuck bitch, you are a really nice fucking piece of shit, bitch fuck'.lower()
tagged_sentence = tagger_HMM.tag(word_tokenize(text))
toxic_index = get_index_toxic_words(text, tagged_sentence)

print(color_toxic_words(toxic_index, text))

fuck bitch, you are a really nice fucking piece of shit, bitch fuck


In [24]:
text = 'have a nice day my dear nigger'.lower()
tagged_sentence = tagger_HMM.tag(word_tokenize(text))
toxic_index = get_index_toxic_words(text, tagged_sentence)

print(color_toxic_words(toxic_index, text))

have a nice day my dear nigger


### Scores

En la competencia usarán el F1 score para evaluar como sigue:

<blockquote cite="http://www.worldwildlife.org/who/index.html">
To evaluate the responses of a system participating in the challenge, we employ the $F_{1}$ score, as in [1]. Let system $A_i$ return a set $S^{t}_{A_{i}}$ of character offsets, for parts of the post found to be toxic. Let $G^{t}$ be the character offsets of the ground truth annotations of $t$. We compute the $F_{1}$ score of system $A_i$ with respect to the ground truth $G$ for post $t$ as follows, where $|·|$ denotes set cardinality.
    
$$ F_{1}^{t}(A_{i}, G) = \dfrac{2 \cdot P^{t}(A_{i}, G) \cdot R^{t}(A_{i}, G)}{P^{t}(A_{i}, G) + R^{t}(A_{i}, G)}$$
    
$$ P^{t}(A_{i}, G) = \dfrac{|S^{t}_{A_{i}} \cap S^{t}_{A_{i}}|}{|S^{t}_{A_{i}}|} $$
    
$$ R^{t}(A_{i}, G) = \dfrac{|S^{t}_{A_{i}} \cap S^{t}_{A_{i}}|}{|S^{t}_{G}|} $$    
    
If $S^{t}_{G}$ is empty for some post $t$ (no gold spans are given for $t$), we set $F_{1}^{t}(A_{i}, G)$ if $S^{t}_{A_{i}}$ is also empty, and $F_{1}^{t}(A_{i}, G) = 0$ otherwise. We finally average $F_{1}^{t}(A_{i}, G)$ over all the posts $t$ of an evaluation dataset $T$ to obtain a single score for system $A_{i}$.

</blockquote>

In [25]:
# La siguiente función viene en el GitHub de la competencia.

def f1(predictions, gold):
    """
    F1 (a.k.a. DICE) operating on two lists of offsets (e.g., character).
    >>> assert f1([0, 1, 4, 5], [0, 1, 6]) == 0.5714285714285714
    :param predictions: a list of predicted offsets
    :param gold: a list of offsets serving as the ground truth
    :return: a score between 0 and 1
    """
    if len(gold) == 0:
        return 1. if len(predictions) == 0 else 0.
    if len(predictions) == 0:
        return 0.
    predictions_set = set(predictions)
    gold_set = set(gold)
    nom = 2 * len(predictions_set.intersection(gold_set))
    denom = len(predictions_set) + len(gold_set)
    return float(nom)/float(denom)

In [26]:
scores_HMM = []

for gold_index, text in test.values:
    tagged_sentence = tagger_HMM.tag(word_tokenize(text.lower()))   
    prediction_index = get_index_toxic_words(text.lower(), tagged_sentence)
    
    print(colored('Pred: ', color='cyan', attrs=['bold']) + 
          color_toxic_words(prediction_index, text))   
    print(colored('Gold: ', color='yellow', attrs=['bold']) + 
          color_toxic_words(gold_index, text) + '\n'*2)
    
    scores_HMM.append(f1(prediction_index, gold_index))

Pred: Because he's a moron and a bigot. It's not any more complicated than that.
Gold: Because he's a moron and a bigot. It's not any more complicated than that.


Pred: How about we stop protecting idiots and let nature add some bleach to the gene pool. We can always submit their names for the Darwin awards.
Gold: How about we stop protecting idiots and let nature add some bleach to the gene pool. We can always submit their names for the Darwin awards.


Pred: If people  were  smart, they would  Boycott this  inept  airline,  but   they  are  not  smart,  so   rogue  businesses  like  this  one,   still thrive   taking the idiots  for  a ride...
Gold: If people  were  smart, they would  Boycott this  inept  airline,  but   they  are  not  smart,  so   rogue  businesses  like  this  one,   still thrive   taking the idiots  for  a ride...


Pred: Trump Claimed that Russia will never invade the Ukraine, when Russia already has - how stupid can people be?
Gold: Trump Claimed that Russia w

Pred: This ridiculous nonsense needs to stop.  It's abusive, has cost me well over $1MM and has destroyed my life.   (By the way, there is no hidden message in my comment.   The situation is exactly what I am saying.)

And yet another idiot is sitting in the parking lot at Carlaw and Colgate Avenue shining lights at my windows.   The gangstalking and harassment endorsed by the Globe and Mail and the individuals and organizations who run this forum needs to stop pronto.
Gold: This ridiculous nonsense needs to stop.  It's abusive, has cost me well over $1MM and has destroyed my life.   (By the way, there is no hidden message in my comment.   The situation is exactly what I am saying.)

And yet another idiot is sitting in the parking lot at Carlaw and Colgate Avenue shining lights at my windows.   The gangstalking and harassment endorsed by the Globe and Mail and the individuals and organizations who run this forum needs to stop pronto.


Pred: You suck
Gold: You suck


Pred: Survival of 

Pred: Why is this black racist crap still on the G&M website?

I stopped talking to black people long ago because I was afraid for my life!!!!!
Since 80%-90% of all crime is by black people it kinda makes sense doesn't it.
Oh wait thats profiling or is it driving while black? 
I don't know you LEFTIST MARXISTS and  BLM nutjobs change the names so fast no one can keep up.
So what do we do when the facts speak like this?
Wash it all away by letting identity Marxists spew their racist hatred of white people?
I think not.
So because you commit most of the crimes in the world why the why the F would we give you the time of day?
Clean up your sh*t first. 
You people are the problem...
Own it
Gold: Why is this black racist crap still on the G&M website?

I stopped talking to black people long ago because I was afraid for my life!!!!!
Since 80%-90% of all crime is by black people it kinda makes sense doesn't it.
Oh wait thats profiling or is it driving while black? 
I don't know you LEFTIST MA

Pred: Race is a social construction -- zero out skin color and some people will just find new and equally stupid reasons to hate.  See, for instance, sectarian violence in Northern Ireland, genocide in Rwanda, etc., for cases where idiots rose above common skin color to express their needs for bigotry.
Gold: Race is a social construction -- zero out skin color and some people will just find new and equally stupid reasons to hate.  See, for instance, sectarian violence in Northern Ireland, genocide in Rwanda, etc., for cases where idiots rose above common skin color to express their needs for bigotry.


Pred: Stupid.  Should expect these ideas from Republicans now, they aren't even trying to hide their buffoonry.  The Beatles wrote about 'tax your shoes'.  Think of all the ladies out there with HUNDREDS of pairs of shoes ...
Gold: Stupid.  Should expect these ideas from Republicans now, they aren't even trying to hide their buffoonry.  The Beatles wrote about 'tax your shoes'.  Think of

Pred: Like I said you can't grasp it. We have to put up with intolerant people here because  they were born here. Is it that hard of a concept. We do not let in those who are intolerant and give them Canadian rights. Your kids will have zero tolerance until your kids grow up and start living in the real world, start paying exhorbitant taxes, exhorbitant prices for homes, food, water, bills, etc. Doesn't mean they'll be racist. Just means they'll learn about debts and how we cannot afford to help every poor soul. It is a numbers game and if you haven't noticed our number is at a trillion and Liberals have been projected at an added 1.5 trillion of debt.  Wake your dumb a$$ up. I studied the charter in school way back when and knew it was for CANADIANS not immigrants.
Gold: Like I said you can't grasp it. We have to put up with intolerant people here because  they were born here. Is it that hard of a concept. We do not let in those who are intolerant and give them Canadian rights. Your k

...

Pred: Lol really. No offence but that’s an idiotic statement. I’m not looking for likes from the douches on the left/ right political side of things. You can’t honestly think this though. Our government federally and provincially across Canada works exactly like this. The more money in the more money spent. It is always, and will always be spent with little oversight, common sense, little efficiency. That’s it. You see provinces with hst taxing more that have massive debts. Obviously more money didn’t make them better money managers, quite the opposite actually. They post phony  surpluses but debts are ever increasing. The problem is the way money is spent. That’s it. Bloated public sectors that’s sole obligation is to become more bloated. What bloats more then more money. Don’t be naive to think less equalization would magically turn these inept politicians to manage money any better. That includes cons, libs, and dippers. They have zero sense of money management and probably never wi

Pred: Well we know he is a wanker
Gold: Well we know he is a wanker


Pred: Look: the village idiot!
Gold: Look: the village idiot!


Pred: It can also be used satirically, to poke fun at the stupid and ignorant. I like to do that now and then.
Gold: It can also be used satirically, to poke fun at the stupid and ignorant. I like to do that now and then.


Pred: This is what's dreadfully wrong with our so-called judicial system; criminals can do harm and get away with it.  I don't  care if the spouse went along to get along with her husband.  Children were sexually abused and didn't even know that the sexual predator was planning to kill them.  The spouse deserves a minimum of 10-years.
Gold: This is what's dreadfully wrong with our so-called judicial system; criminals can do harm and get away with it.  I don't  care if the spouse went along to get along with her husband.  Children were sexually abused and didn't even know that the sexual predator was planning to kill them.  The spouse 

Pred: Sorry old man....I knew you were a DRUNK!
During  the 5 years in Alaska we have grossed 1.5 million dollars
www.thehealingcentermedicalclinic.org
Gold: Sorry old man....I knew you were a DRUNK!
During  the 5 years in Alaska we have grossed 1.5 million dollars
www.thehealingcentermedicalclinic.org


Pred: As a general rule: nearly all assisted living homes are a (legal) scam. As an EMT, I go to these horrible places on the daily.  The rules and regulations are thin, the medical care received is suspect, and the money commanded by these glorified halfway houses for the elderly is laughable. 
 Where I work, there is one on nearly every suburban street. There are so many, even if the regulators were doing their job, they have far too few to tackle this epidemic. This is why things like this happen. I assure you that this is not an isolated case of fraud.
 What is worse, however, is the neglect and abuse that our older generations are suffering. It's disgusting. We allow people with m

Pred: Because people tend to be emotion-driven idiots which is why politicians and activists are always aiming at your heartstrings.
Gold: Because people tend to be emotion-driven idiots which is why politicians and activists are always aiming at your heartstrings.


Pred: You lie, and in a sniveling tone. I bring up Hillary, because Mr. Hahn would have her and her Islamic friends run the U.S. Sad, and pathetic.
Gold: You lie, and in a sniveling tone. I bring up Hillary, because Mr. Hahn would have her and her Islamic friends run the U.S. Sad, and pathetic.


Pred: Yeah, all you knuckleheads, go ahead & make MYYYYY Day!!!! It will be HYYYUUUGE, just like all of my HYYYUUUGE casino bankruptcies. Getting all other's to take the fault and financial fall for me. By losing MONEY, THIS TRUMP,  will have the United States, filing for bankruptcy within 365 days of taking office. When I refuse to let the Treasury Secretary pay the interest on the amount of debt we are beholden to them [Chinese]

Pred: Edwin, you are a joke.  First you make claims about longevity that have long ago been debunked because yiu couldn't be bothered to read the whole story.  You change your tune and say you cant judge reliabilty by high milegae. You keep changing the factors to try and perpetuate your lies. Before you were comparing high mileage to longevity and now you want to change that. 

Totally Unbelievable like most of the garbage and unsupported comments you spew forth.
Gold: Edwin, you are a joke.  First you make claims about longevity that have long ago been debunked because yiu couldn't be bothered to read the whole story.  You change your tune and say you cant judge reliabilty by high milegae. You keep changing the factors to try and perpetuate your lies. Before you were comparing high mileage to longevity and now you want to change that. 

Totally Unbelievable like most of the garbage and unsupported comments you spew forth.


Pred: Most of them are too stupid to understand what is goin

In [27]:
print('HMM score: {:.2f}'.format(np.mean(scores_HMM)))

HMM score: 0.32


## Conditional Random Fields for Sequence Prediction

In [28]:
from itertools import chain
from nltk import pos_tag
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.preprocessing import LabelBinarizer
import sklearn
import pycrfsuite
from tqdm import tqdm

In [29]:
train_sents = list(nltk.corpus.conll2002.iob_sents('esp.train'))

In [30]:
def word2features(sent, i):
    word = sent[i][0]
    postag = sent[i][1]
    features = [
        'bias',
        'word.lower=' + word.lower(),
        'word[-3:]=' + word[-3:],
        'word[-2:]=' + word[-2:],
        'word.isupper=%s' % word.isupper(),
        'word.istitle=%s' % word.istitle(),
        'word.isdigit=%s' % word.isdigit(),
        'postag=' + postag,
        'postag[:2]=' + postag[:2],
    ]
    if i > 0:
        word1 = sent[i-1][0]
        postag1 = sent[i-1][1]
        features.extend([
            '-1:word.lower=' + word1.lower(),
            '-1:word.istitle=%s' % word1.istitle(),
            '-1:word.isupper=%s' % word1.isupper(),
            '-1:postag=' + postag1,
            '-1:postag[:2]=' + postag1[:2],
        ])
    else:
        features.append('BOS')
        
    if i < len(sent)-1:
        word1 = sent[i+1][0]
        postag1 = sent[i+1][1]
        features.extend([
            '+1:word.lower=' + word1.lower(),
            '+1:word.istitle=%s' % word1.istitle(),
            '+1:word.isupper=%s' % word1.isupper(),
            '+1:postag=' + postag1,
            '+1:postag[:2]=' + postag1[:2],
        ])
    else:
        features.append('EOS')
                
    return features


def sent2features(sent):
    return [word2features(sent, i) for i in range(len(sent))]

def sent2labels(sent):
    return [label for token, postag, label in sent]

def sent2tokens(sent):
    return [token for token, postag, label in sent]

def token_postag_label(sentence):
    return pos_tag(word_tokenize(sentence))

In [31]:
train_data_crf = []
for text, toxic_tags in tqdm(zip(train['text'], train_data), total=len(train_data)):
    pos_tags = token_postag_label(text.lower())
    sentence = []
    for x,y in zip(pos_tags, toxic_tags):
        sentence.append(x + (y[1],))
        
    train_data_crf.append(sentence)

100%|██████████| 7939/7939 [00:09<00:00, 805.01it/s]


In [32]:
X_train = [sent2features(s) for s in train_data_crf]
y_train = [sent2labels(s) for s in train_data_crf]

# test_sents = list(nltk.corpus.conll2002.iob_sents('esp.testb'))

# X_test = [sent2features(s) for s in test_sents]
# y_test = [sent2labels(s) for s in test_sents]

In [33]:
trainer = pycrfsuite.Trainer(verbose=False)

for xseq, yseq in zip(X_train, y_train):
    trainer.append(xseq, yseq)

Probablemente sea buena idea hacer una búsqueda de los mejores hiperparámetros, ya que el performance cambia significativamente dependiendo de los hiperparámetros.

In [34]:
trainer.set_params({
    'c1': 1.0,   # coefficient for L1 penalty
    'c2': 0.01,  # coefficient for L2 penalty
    'max_iterations': 100,  # stop earlier
    # include transitions that are possible, but not observed
    'feature.possible_transitions': True
})

In [35]:
trainer.params()

['feature.minfreq',
 'feature.possible_states',
 'feature.possible_transitions',
 'c1',
 'c2',
 'max_iterations',
 'num_memories',
 'epsilon',
 'period',
 'delta',
 'linesearch',
 'max_linesearch']

In [36]:
%time trainer.train('toxic_speech.crfsuite')

CPU times: user 12.4 s, sys: 0 ns, total: 12.4 s
Wall time: 12.4 s


In [37]:
tagger_crf = pycrfsuite.Tagger()
tagger_crf.open('toxic_speech.crfsuite')

In [38]:
# test_sents = list(nltk.corpus.conll2002.iob_sents('esp.testb'))

# X_test = [sent2features(s) for s in test_sents]
# y_test = [sent2labels(s) for s in test_sents]

In [39]:
example_sent = [('bitch', 'NN', ''),
                ('pls', 'VBP', ''),
                (',', ',', ''),
                ('you', 'NN', ''),
                ('are', 'VBP', ''),
                ('a', 'DT', ''),
                ('fucking', 'JJ', ''),
                ('piece', 'NN', ''),
                ('of', 'IN', ''),
                ('shit', 'NN', '')]

words = [x[0] for x in example_sent]
tags = tagger_crf.tag(sent2features(example_sent))
tagged_sentence = [(word, tag) for word,tag in zip(words,tags)]

tagged_sentence

[('bitch', 'toxic'),
 ('pls', 'non_toxic'),
 (',', 'non_toxic'),
 ('you', 'non_toxic'),
 ('are', 'non_toxic'),
 ('a', 'non_toxic'),
 ('fucking', 'toxic'),
 ('piece', 'toxic'),
 ('of', 'toxic'),
 ('shit', 'toxic')]

### Scores

In [40]:
test_data_crf =  []
for text in tqdm(test['text']):
    pos_tags = token_postag_label(text.lower())
    sentence = []
    for x in pos_tags:
        sentence.append(x + ('',))
        
    test_data_crf.append(sentence)

100%|██████████| 690/690 [00:00<00:00, 884.22it/s]


In [41]:
scores_CRF = []

for text_crf,(gold_index,text) in zip(test_data_crf, test.values):
    words = [x[0] for x in text_crf]
    tags = tagger_crf.tag(sent2features(text_crf))
    
    tagged_sentence = [(word, tag) for word,tag in zip(words,tags)]
    prediction_index = get_index_toxic_words(text.lower(), tagged_sentence)
    
    print(colored('Pred: ', color='cyan', attrs=['bold']) + 
          color_toxic_words(prediction_index, text))   
    print(colored('Gold: ', color='yellow', attrs=['bold']) + 
          color_toxic_words(gold_index, text) + '\n'*2)
    
    scores_CRF.append(f1(prediction_index, gold_index))

Pred: Because he's a moron and a bigot. It's not any more complicated than that.
Gold: Because he's a moron and a bigot. It's not any more complicated than that.


Pred: How about we stop protecting idiots and let nature add some bleach to the gene pool. We can always submit their names for the Darwin awards.
Gold: How about we stop protecting idiots and let nature add some bleach to the gene pool. We can always submit their names for the Darwin awards.


Pred: If people  were  smart, they would  Boycott this  inept  airline,  but   they  are  not  smart,  so   rogue  businesses  like  this  one,   still thrive   taking the idiots  for  a ride...
Gold: If people  were  smart, they would  Boycott this  inept  airline,  but   they  are  not  smart,  so   rogue  businesses  like  this  one,   still thrive   taking the idiots  for  a ride...


Pred: Trump Claimed that Russia will never invade the Ukraine, when Russia already has - how stupid can people be?
Gold: Trump Claimed that Russia w

Pred: You prove my point that it is a matter of personal judgement, you don't think that 'certain' person is a troll, I do think he is. I'll grant you he is ostensibly civil but his aim is to pour scorn on and subtly abuse orthodox Catholic posters. Yet for all that I do not flag him nor do I mute him just because I think his comments are generally pathetic.
Gold: You prove my point that it is a matter of personal judgement, you don't think that 'certain' person is a troll, I do think he is. I'll grant you he is ostensibly civil but his aim is to pour scorn on and subtly abuse orthodox Catholic posters. Yet for all that I do not flag him nor do I mute him just because I think his comments are generally pathetic.


Pred: He should have died in Afghanistan and be with Satan now--but we are stuck with this deviant killer.
Gold: He should have died in Afghanistan and be with Satan now--but we are stuck with this deviant killer.


Pred: Laughable.   The great negotiator  can't keep employee

Gold: Good morning, ducati, Moto guzzi, triumph and Norton. No hogs, not cheap and not female. Have a good day shark.


Pred: another stupid comment
Gold: another stupid comment


Pred: An idiot from new york
Gold: An idiot from new york


Pred: Lol, such an idiotic comment.  There's junk food sold all over the damn world.   I live in the village and never fed my kids junk like that. My kids have always had good teeth and still do.   Same goes for majority of my friends and relatives.  You compare us 'filthy natives' to the crack whores in the city whose kids are raised on nasty ass junk food (or no food at all)  well, I'd even tip that bigot at Stampede Aviation to bring me back to the ville.
Gold: Lol, such an idiotic comment.  There's junk food sold all over the damn world.   I live in the village and never fed my kids junk like that. My kids have always had good teeth and still do.   Same goes for majority of my friends and relatives.  You compare us 'filthy natives' to the crack w

In [42]:
print('CRF score: {:.2f}'.format(np.mean(scores_CRF)))

CRF score: 0.55


## LSTM

Ver [Sequence Tagging with Tensorflow](https://guillaumegenthial.github.io/sequence-tagging-with-tensorflow.html)